In [1]:
using Plotly
using LinearAlgebra

WebIO._IJuliaInit()

In [2]:
# define needed equations

const µ = 3.986004419 * 10^14 # standard gravitational parameter earth [m^3/s^2]
const R_e = 6371000. # average earth radius [m]
const g_0 = 9.80665  # m

"""
    Euler Equations with zero torque conditions used with numerical propogator
    to propogate angular velocity
"""
function EulerEquationsZeroTorque(ω, time, I)
    # calculate dω/dt
    dωdt = [ ((I[2]-I[3])/I[1])*ω[2]*ω[3], ((I[3]-I[1])/I[2])*ω[1]*ω[3], ((I[1]-I[2])/I[3])*ω[2]*ω[1] ]
end

# RKF45 constants (to be stored in seperate file)
const A2 = 2. / 9.
const A3 = 1. / 3.
const A4 = 3. / 4.
const A5 = 1.
const A6 = 5. / 6.
const B21 = 2. / 9.
const B31 = 1. / 12.
const B41 = 69. / 128.
const B51 = -17. / 12.
const B61 = 65. / 432.
const B32 = 1. / 4.
const B42 = -243. / 128.
const B52 = 27. / 4.
const B62 = -5. / 16.
const B43 = 135. / 64.
const B53 = -27. / 5.
const B63 = 13. / 16.
const B54 = 16. / 15.
const B64 = 4. / 27.
const B65  = 5. / 144.
const CH1 = 47. / 450.
const CH2 = 0.
const CH3 = 12. / 25.
const CH4 = 32. / 225.
const CH5 = 1. / 30.
const CH6 = 6. / 25.
const CT1 = -1. / 150.
const CT2 = 0.
const CT3 = 3. / 100.
const CT4 = -16. / 75.
const CT5 = -1. / 20.
const CT6 = 6. / 25.

# https://en.wikipedia.org/wiki/Runge%E2%80%93Kutta%E2%80%93Fehlberg_method
function RK45(x, time, step, dxdt)
    # compute k1 through k6
    k1 = step * dxdt(x, time)
    modifier = B21 * k1
    k2 = step * dxdt(x + modifier, time + (A2 * step))
    modifier = B31 * k1 + B32 * k2
    k3 = step * dxdt(x + modifier, time + (A3 * step))
    modifier = B41 * k1 + B42 * k2 + B43 * k3
    k4 = step * dxdt(x + modifier, time + (A4 * step))
    modifier = B51 * k1 + B52 * k2 + B53 * k3 + B54 * k4
    k5 = step * dxdt(x + modifier, time + (A5 * step))
    modifier = B61 * k1 + B62 * k2 + B63 * k3 + B64 * k4 + B65 * k5
    k6 = step * dxdt(x + modifier, time + (A6 * step))
    # compute weighted average
    x_new = x + CH1 * k1 + CH2 * k2 + CH3 * k3 + CH4 * k4 + CH5 * k5 + CH6 * k6
    # compute error
    error = abs.(CT1 * k1 + CT2 * k2 + CT3 * k3 + CT4 * k4 + CT5 * k5 + CT6 * k6)
    # NOTE: we can add in adaptive time steps here if we want...
    # return new x values and numerical integration error
    return(x_new, error)
end

function Euler321_2_Quat(euler321)
    # define reused quantities
    ϕ_2 = euler321[1]/2
    θ_2 = euler321[2]/2
    ψ_2 = euler321[3]/2
    cos_ϕ_2 = cos(ϕ_2)
    sin_ϕ_2 = sin(ϕ_2)
    cos_θ_2 = cos(θ_2)
    sin_θ_2 = sin(θ_2)
    cos_ψ_2 = cos(ψ_2)
    sin_ψ_2 = sin(ψ_2)
    # conver to quaternion representation
    q0 = cos_ϕ_2*cos_θ_2*cos_ψ_2 + sin_ϕ_2*sin_θ_2*sin_ψ_2
    q1 = cos_ϕ_2*cos_θ_2*sin_ψ_2 - sin_ϕ_2*sin_θ_2*cos_ψ_2
    q2 = cos_ϕ_2*sin_θ_2*cos_ψ_2 + sin_ϕ_2*cos_θ_2*sin_ψ_2
    q3 = sin_ϕ_2*cos_θ_2*cos_ψ_2 - cos_ϕ_2*sin_θ_2*sin_ψ_2 
    return([q0, q1, q2, q3])
end

"""
    Quaternion Kinematic Equations used with numerical propogator
    to propogate attitude

    Note: q = [q_0, q_1, q_2, q_3], where q_0 is the scalar term and q_1, q_2, q_3
          are the vector terms
"""
function QuaternionKinematics(q, time; ω)
    # calculate dω/dt
    Ω = [ 0 -ω[1] -ω[2] -ω[3] ;
         ω[1] 0 ω[3] -ω[2] ;
        ω[2] -ω[3] 0 ω[1] ;
        ω[3] ω[2] -ω[1] 0]
    dqdt = 0.5 * Ω * q
    return(dqdt)
end

struct KeplarianOrbit
    a # semi-major axis [meters]
    e # eccentricity [-]
    i # inclinations [rad]
    ω # arg. of perigee [rad]
    Ω # raan [rad]
    ν # true anomaly [rad]
end

struct EquinoctialOrbit
    p # semi latus rectum [meters]
    f
    g
    h
    k
    L # true longitude [rad]
end

function Keplarian2Equinoctial(orbit::KeplarianOrbit)
    # unload orbit parameters
    a = orbit.a
    e = orbit.e
    i = orbit.i
    ω = orbit.ω
    Ω = orbit.Ω
    ν = orbit.ν
    # convert orbital elements
    p = a*(1-e^2)
    f = e*cos(ω+Ω)
    g = e*sin(ω+Ω)
    h = tan(i/2)*cos(Ω)
    k = tan(i/2)*sin(Ω)
    L = Ω + ω + ν
    return(EquinoctialOrbit(p,f,g,h,k,L))
end

"""
    Quaternion Kinematic Equations used with numerical propogator
    to propogate attitude

    Note: q = [q_0, q_1, q_2, q_3], where q_0 is the scalar term and q_1, q_2, q_3
          are the vector terms
"""
function QuaternionKinematics(q, time; ω)
    # calculate dω/dt
    Ω = [ 0 -ω[1] -ω[2] -ω[3] ;
         ω[1] 0 ω[3] -ω[2] ;
        ω[2] -ω[3] 0 ω[1] ;
        ω[3] ω[2] -ω[1] 0]
    dqdt = 0.5 * Ω * q
    return(dqdt)
end

"""
Gauss Variational Equations for Modified Equinoctial Elements for numerical
propogation with perturbing forces.

# Arguments
- `orbit`: current orbital position in modified equinoctial elements
    (see EquinoctialOrbit structure in Structures.jl) as a six position array
- `time`: current time in MJD [days]
- `accel`: additional perturbing acceleration in RTN frame, array of three
    acceleration values [m/s^2], defaulted to zero
- `air_drag`: flag to include perturbing drag acceleration, defaulted to false
- `J2`: flag to include J2 earth obliquity perturbing, defaulted to false
"""
function GaussVariationalEquationsEquinoctial(orbit, time; accel=[0.,0.,0.], accel_drag=false, accel_J2=false)
    # unpack orbit
    p = orbit[1] # semi latus rectum [meters]
    f = orbit[2]
    g = orbit[3]
    h = orbit[4]
    k = orbit[5]
    L = orbit[6] # true longitude [rad]

    # calcualte useful quantities
    cosL = cos(L)
    sinL = sin(L)
    w = 1 + f*cosL+g*sinL
    root_p_µ = sqrt(p/µ)
    s_2 = 1 + h^2 + k^2

    # calculate matrix
    A = [0 2*p/w 0;
        sinL (1/w)*((w+1)*cosL+f) -(g/w)*(h*sinL-k*cosL);
        -cosL (w+1)*sinL+g (f/w)*(h*sinL-k*cosL);
        0 0 (s_2*cosL)/(2*w);
        0 0 (s_2*sinL)/(2*w);
        0 0 h*sinL-k*cosL]

    A = root_p_µ * A
    b = [0, 0, 0, 0, 0, sqrt(µ*p)*(w/p)^2]

    # add perturbations to acceleration term
    if accel_drag
        accel = accel + accel_drag_RTN_Equinoctial(orbit, 1., 10., 1.5)
    end
    if accel_J2
        accel = accel + accel_J2_RTN_Equinoctial(orbit)
    end

    # calculate doe/dt
    dOEdt = A*accel + b
end


"""
    Euler Equations with applied torque conditions used with numerical propogator
    to propogate angular velocity
"""
function EulerEquations(ω, time, I, M)
    # calculate dω/dt
    dωdt = [(M[1]-((I[3]-I[2])*ω[2]*ω[3]))/I[1], (M[2]-((I[1]-I[3])*ω[3]*ω[1]))/I[2], (M[3]-((I[2]-I[1])*ω[1]*ω[2]))/I[3]]
end

"""
Converts UT1 in MJD to GMST in radians mod 2pi
TODO: add source and better description

# Arguments
- `MJD`: UT1 in modified julian date format, float [years]

# Returns
- GMST, float [radians]
"""
function UT1_MJD_to_GMST(MJD)
    d = MJD - 51544.5
    # GMST in degrees
    GMST = 280.4606 + 360.9856473*d
    # mod 2pi
    return(mod2pi(deg2rad(GMST)))
end

"""
GMST to Rotation Matrix CRF --> TRF
(Used to convert ECI to ECEF)
"""
function GMST_to_rotation_matrix(GMST)
    # rotation about z axis by angle given by GMST
    return([cos(-GMST) -sin(-GMST) 0;
            sin(-GMST) cos(-GMST) 0;
            0 0 1.])
end

"""
Convert ECI position to ECEF position given UT1 MJD time
"""
function ECI_to_ECEF(MJD, R_ECI)
    # convert UT1 in MJD to GMST
    GMST = UT1_MJD_to_GMST(MJD)
    # calculate rotation matrix to convert ECI at time to ECEF
    A = GMST_to_rotation_matrix(GMST)
    # return output in ECEF
    return(A * R_ECI)
end

"""
ECEF to Geodetic Coordinates with tolerance on the accuracy of the latitude

Takes into account the eccentricity of the earth
"""
# plug in ECEF position vector and tolerance number, defaulted to 10^-11
function ECEF_to_Geodetic(r, ε = 10^-11)
    e_elipsiod = 0.08182
    r_e = 6378.136*1000. #m
    # calculate longitude
    λ = atan(r[2],r[1])
    # calculate initial guess of latitude based on circular earth
    ϕ_prev = atan(r[3], norm([r[1]; r[2]]))
    N = r_e/(1 - (e_elipsiod^2 * sin(ϕ_prev)^2))^0.5
    ϕ = atan((r[3] + N * e_elipsiod^2 * sin(ϕ_prev)),norm([r[1]; r[2]]))
    while(abs(ϕ_prev - ϕ) > ε)
        ϕ_prev = ϕ
        N = r_e/(1 - (e_elipsiod^2 * sin(ϕ_prev)^2))^0.5
        ϕ = atan((r[3] + N * e_elipsiod^2 * sin(ϕ_prev))/norm([r[1]; r[2]]))
    end
    # use converged on ϕ to find height
    h = ((norm([r[1]; r[2]])/cos(ϕ))-N)
    return([h;ϕ;λ])
end

"""
Converts ECI to Geodetic
(wrapper of ECI_to_ECEF and ECEF_to_Geodetic)
TODO: double check units of documentation

# Arguments
- `MJD`: date at which conversion required in MJD [days]
- `R_ECI`: ECI positional 3 element array of object [meters]

# Returns
- Array of Geodetic position coordinates, [h;ϕ;λ] [height off of ellipsoid earth
surface [m], latitude [deg], longitude [deg]]
"""
function ECI_to_Geodetic(MJD, R_ECI)
    # convert ECI to ECEF
    R_ECEF = ECI_to_ECEF(MJD, R_ECI)
    # convert ECEF to Geodetic
    return(ECEF_to_Geodetic(R_ECEF))
end

function Equinoctial2ECI(orbit::EquinoctialOrbit)
    # unload orbit parameters
    p = orbit.p
    f = orbit.f
    g = orbit.g
    h = orbit.h
    k = orbit.k
    L = orbit.L
    # calculate important values
    α_2 = h^2 - k^2
    s_2 = 1 + h^2 + k^2
    w = 1 + f*cos(L) + g*sin(L)
    r = p/w
    # convert orbital elements
    r_x = (r/s_2)*(cos(L)+α_2*cos(L)+2*h*k*sin(L))
    r_y = (r/s_2)*(sin(L)-α_2*sin(L)+2*h*k*cos(L))
    r_z = (2*r/s_2)*(h*sin(L)-k*cos(L))
    v_x = (-1/s_2)*sqrt(µ/p)*(sin(L)+α_2*sin(L)-2*h*k*cos(L)+g-2*f*h*k+α_2*g)
    v_y = (-1/s_2)*sqrt(µ/p)*(-cos(L)+α_2*cos(L)+2*h*k*sin(L)-f+2*g*h*k+α_2*f)
    v_z = (2/s_2)*sqrt(µ/p)*(h*cos(L)+k*sin(L)+f*h+g*k)
    return([r_x, r_y, r_z, v_x, v_y, v_z])
end

Equinoctial2ECI (generic function with 1 method)

In [3]:
I_body_sapling = 10^-9 * [1.67e+06 -9952.526 1977.479;
                          -9952.526 1.67e+06 28959.744;
                          1977.479 28959.744 1.78e+06]

Inertia_Tensor_Principle_Sapling = diagm(eigvals(I_body_sapling))
Principle_Axes_wrt_Body_Sapling = eigvecs(I_body_sapling)
R_body_to_Principle_Sapling = transpose(Principle_Axes_wrt_Body_Sapling)

3×3 transpose(::Matrix{Float64}) with eltype Float64:
  0.57754      0.793001  -0.193898
  0.816352    -0.559835   0.141965
 -0.00402743   0.240279   0.970695

In [4]:
# calculate produced torque from magnetorquers...
m_body = [1,0,0]
m_principle = R_body_to_Principle_Sapling * m_body
B_external_body = [0,0,1]
B_external_principle = R_body_to_Principle_Sapling * B_external_body
print(B_external_principle)
# torque generated
# M_magnetic = cross(m,B_external_principle)

[-0.19389773478002711, 0.14196465587860457, 0.9706954748676042]

In [5]:
# calculate B_Dot, assume constant magnetic field
ω = [1,0,0] # omega in body frame
b = [0,1,0] # b in body frame
B_dot = cross(-ω,b) # in satellite frame (golen rule)

3-element Vector{Int64}:
  0
  0
 -1

In [6]:
# define test initial conditions
ω_0 = [deg2rad(5.),deg2rad(4.),deg2rad(3.)] # rad/sec
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
EulerEquationsZeroTorque_sapling(ω, time) = EulerEquationsZeroTorque(ω, time, I_sapling)

# propogate using RK45
time_initial = 0. # sec
time_end = time_initial + 90*60. # stop integrator after 90 minutes
step_size = 1 # sec
ω_history_sapling = [ω_0]
error_history_sapling = [[0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
while time < time_end
    global time = time_history[end]
    ω_sapling = ω_history_sapling[end]
    ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquationsZeroTorque_sapling)
    push!(time_history, time + step_size)
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_sapling, error_sapling)
end
print("Integration finished!\n")

# plot numerical integration outputs
ω_x_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,1), mode="lines", name="ω_x")
ω_y_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,2), mode="lines", name="ω_y")
ω_z_vs_time =scatter(x=time_history, y=getindex.(ω_history_sapling,3), mode="lines", name="ω_z")
layout = Layout(title="Sapling Zero Torque ω Propogation", xaxis_title="time [sec]", yaxis_title="ω [rad/sec]")
plot([ω_x_vs_time, ω_y_vs_time, ω_z_vs_time],layout)

Starting integration...
Integration finished!


data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [7]:
euler_angle_initial = [0.3, 0.4, 0.5] # rad
quaternion_initial = Euler321_2_Quat(euler_angle_initial)
# define initial orbital conditions
orbit = KeplarianOrbit(
                500.e3 + R_e,
                0.05,
                deg2rad(50.),
                deg2rad(0.),
                deg2rad(0.),
                deg2rad(0)
                )

time = 59716.0 #[days] MJD
# convert to equinoctial
orbit_initial_equinoctial = Keplarian2Equinoctial(orbit)
orbit_initial = [orbit_initial_equinoctial.p,
                orbit_initial_equinoctial.f,
                orbit_initial_equinoctial.g,
                orbit_initial_equinoctial.h,
                orbit_initial_equinoctial.k,
                orbit_initial_equinoctial.L]

# propogate using RK45
time_initial = time # days
time_end = time_initial + ((60. * 30) / (24*60*60)) # stop integrator after 30 min
step_size = 10 # sec
ω_history_sapling = [ω_0]
quaternion_history_sapling = [quaternion_initial]
error_history_ω_sapling = [[0.,0.,0.]]
error_history_quaternion_sapling = [[0.,0.,0.]]
orbit_history = [orbit_initial]
error_history_orbit = [[0.,0.,0.,0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
EulerEquationsZeroTorque_sapling(ω, time) = EulerEquationsZeroTorque(ω, time, I_sapling)
while time < time_end
    global time = time_history[end]
    # angular velocity numerical integration
    ω_sapling = ω_history_sapling[end]
    ω_new_sapling, error_ω_sapling = RK45(ω_sapling, time, step_size, EulerEquationsZeroTorque_sapling)
    # quaternion numerical integration
    QuaternionKinematics_ω(q, time) = QuaternionKinematics(q, time, ω = ω_sapling)
    quaternion_sapling = quaternion_history_sapling[end]
    quaternion_new_sapling, error_quaternion_sapling = RK45(quaternion_sapling, time, step_size, QuaternionKinematics_ω)
    # equinoctial orbit numerical integration
    orbit = orbit_history[end]
    orbit_new, error = RK45(orbit, time, step_size, GaussVariationalEquationsEquinoctial)
    push!(orbit_history, orbit_new)
    push!(error_history_orbit, error)
    
    # push results
    push!(time_history, time + step_size/(24*60*60))
    
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_ω_sapling, error_ω_sapling)
    
    push!(quaternion_history_sapling, normalize!(quaternion_new_sapling))
    push!(error_history_quaternion_sapling, error_quaternion_sapling) 
end
print("Integration finished!\n")

# plot numerical integration outputs
q_1_vs_time = scatter(x=time_history .- time_history[1], y=getindex.(quaternion_history_sapling,1), mode="lines", name="q_1")
q_2_vs_time = scatter(x=time_history .- time_history[1], y=getindex.(quaternion_history_sapling,2), mode="lines", name="q_2")
q_3_vs_time =scatter(x=time_history .- time_history[1], y=getindex.(quaternion_history_sapling,3), mode="lines", name="q_3")
q_4_vs_time =scatter(x=time_history .- time_history[1], y=getindex.(quaternion_history_sapling,4), mode="lines", name="q_4")
layout = Layout(title="Sapling Zero Torque Quaternion Propogation", xaxis_title="time [days]", yaxis_title="q [rad]")

plot([q_1_vs_time, q_2_vs_time, q_3_vs_time, q_4_vs_time],layout)

Starting integration...
Integration finished!


data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [8]:
# convert equinoctial orbit elements to geodetic coordinates, then calculate local magnetic field
# store ECI terms
ECI_history= []
for orbit in orbit_history
    equinoctial_orbit = EquinoctialOrbit(orbit[1], orbit[2], orbit[3], orbit[4], orbit[5], orbit[6])
    ECI_orbit = Equinoctial2ECI(equinoctial_orbit)
    push!(ECI_history, [ECI_orbit[1],ECI_orbit[2],ECI_orbit[3]])
end

print("Plotting...\n")
n = 10
u = collect(range(0,2*π, length = n))
v = collect(range(0,π, length = n))
r_e = 6378.

u_range = range(0, stop=2π, length=100)
u = u_range' .* ones(100)
v_range = range(0, stop=π, length=100)
v = ones(100)' .* v_range

x = @. r_e * cos(u) * sin(v)
y = @. r_e * sin(u) * sin(v)
z = @. r_e * cos(v)

layout = Layout(title="Demonatration of Numerical Propogator Dwell")
trace1 = surface(x=x, y=y, z=z, showscale=false)
trace2 = scatter3d(x=(getindex.(ECI_history,1) ./ 1000), y=(getindex.(ECI_history,2) ./ 1000), z=(getindex.(ECI_history,3) ./ 1000),
    mode="markers",
    marker=attr(
        size=1,
    ))
plot([trace1, trace2], layout)

Plotting...


data: [
  "surface with fields showscale, type, x, y, and z",
  "scatter3d with fields marker, mode, type, x, y, and z"
]

layout: "layout with fields margin, template, and title"

In [9]:
ECEF_history = []
for (MJD, ECI) in zip(time_history, ECI_history)
    push!(ECEF_history, ECI_to_ECEF(MJD, ECI))
end

print("Plotting...\n")
n = 10
u = collect(range(0,2*π, length = n))
v = collect(range(0,π, length = n))
r_e = 6378.

u_range = range(0, stop=2π, length=100)
u = u_range' .* ones(100)
v_range = range(0, stop=π, length=100)
v = ones(100)' .* v_range

x = @. r_e * cos(u) * sin(v)
y = @. r_e * sin(u) * sin(v)
z = @. r_e * cos(v)

layout = Layout(title="Demonatration of Numerical Propogator", scene=attr(attr(xaxis_title="X [ECEF]", yaxis_title="Y [ECEF]", zaxis_title="Y [ECEF]")))
trace1 = surface(x=x, y=y, z=z, showscale=false)
trace2 = scatter3d(x=(getindex.(ECEF_history,1) ./ 1000), y=(getindex.(ECEF_history,2) ./ 1000), z=(getindex.(ECEF_history,3) ./ 1000),
    mode="markers",
    marker=attr(
        size=1,
    ))
plot([trace1, trace2], layout)

Plotting...


data: [
  "surface with fields showscale, type, x, y, and z",
  "scatter3d with fields marker, mode, type, x, y, and z"
]

layout: "layout with fields margin, scene, template, and title"

In [10]:
geodetic_history = []
for (MJD, ECI) in zip(time_history, ECI_history)
    geodetic = ECI_to_Geodetic(MJD, ECI)
    push!(geodetic_history, [geodetic[1], rad2deg(geodetic[2]), rad2deg(geodetic[3])])
end

layout = Layout(title="Propogated Geodetic Coordinates")
trace1 = scattergeo(lat=getindex.(geodetic_history,2),lon=getindex.(geodetic_history,3),hovertext=time_history.-time_history[1])
plot([trace1], layout)

data: [
  "scattergeo with fields hovertext, lat, lon, and type"
]

layout: "layout with fields margin, template, and title"

In [11]:
using SatelliteToolbox

In [12]:
mag_hist = []
for (MJD, ECEF) in zip(time_history, ECEF_history)
    mag = geomag_dipole(ECEF)/1000
    push!(mag_hist, [mag[1], mag[2], mag[3]])
end

# plot mag outputs
mag_x = scatter(x=time_history.-time_history[1], y=getindex.(mag_hist,1), mode="lines", name="mag_x")
mag_y = scatter(x=time_history.-time_history[1], y=getindex.(mag_hist,2), mode="lines", name="mag_y")
mag_z =scatter(x=time_history.-time_history[1], y=getindex.(mag_hist,3), mode="lines", name="mag_z")
layout = Layout(title="Magnetic Propogation", xaxis_title="time [days]", yaxis_title="Magnetic Field [uT]")

plot([mag_x, mag_y, mag_z],layout)

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [13]:
# define test initial conditions
ω_0 = [deg2rad(10.),deg2rad(0.),deg2rad(0.)] # rad/sec
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
M = [0.0001,0,.0001]
EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, M)

# propogate using RK45
time_initial = 0. # sec
time_end = time_initial + 90. # stop integrator after 90 sec
step_size = 1 # sec
ω_history_sapling = [ω_0]
error_history_sapling = [[0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
while time < time_end
    global time = time_history[end]
    ω_sapling = ω_history_sapling[end]
    ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    push!(time_history, time + step_size)
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_sapling, error_sapling)
end
print("Integration finished!\n")

# plot numerical integration outputs
ω_x_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,1), mode="lines", name="ω_x")
ω_y_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,2), mode="lines", name="ω_y")
ω_z_vs_time =scatter(x=time_history, y=getindex.(ω_history_sapling,3), mode="lines", name="ω_z")
layout = Layout(title="Sapling Zero Torque ω Propogation", xaxis_title="time [sec]", yaxis_title="ω [rad/sec]")
plot([ω_x_vs_time, ω_y_vs_time, ω_z_vs_time],layout)

Starting integration...
Integration finished!


data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [14]:
# given constant magnetic field, do -BDot torque for one time step and progate...should see angular velocity 

# define test initial conditions
b_norm = 7*10^-5 # Tesla
M_max = 1. # A*m^2
ω_0 = [deg2rad(3.),deg2rad(3.),deg2rad(3.)] # rad/sec
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
tol = deg2rad(0.001) # rad/sec

# propogate using RK45
time_initial = 0. # sec
time_end = time_initial + 5*60 # stop integrator after 1 min
step_size = 1 # sec
ω_history_sapling = [ω_0]
error_history_sapling = [[0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
while time < time_end
    global time = time_history[end]
    ω_sapling = ω_history_sapling[end]
    b_inertial = [rand(),rand(),rand()]
    b_inertial = b_norm*(b_inertial/norm(b_inertial))
    B_dot_body_norm = cross(-ω_sapling,b_inertial)/norm(cross(-ω_sapling,b_inertial))
    M_sat = -(1 - (norm(ω_0)-norm(ω_sapling))/norm(ω_0))*B_dot_body_norm
    print(norm(M_sat),"\n")
    M_B_dot_body = cross(M_sat,b_inertial)
    #     print(M_B_dot_body, "\n")
    #     M_B_dot_principle = R_body_to_Principle_Sapling * M_B_dot_body
    #     #     print(M_B_dot_principle, "    ", ω_sapling, "\n")
    #     if (norm(ω_sapling) < tol)
    #         M_B_dot_principle = [0,0,0]
    #     end
    EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, M_B_dot_body)
    ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    push!(time_history, time + step_size)
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_sapling, error_sapling)
end
print("Integration finished!\n")

# plot numerical integration outputs
ω_x_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,1), mode="lines", name="ω_x")
ω_y_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,2), mode="lines", name="ω_y")
ω_z_vs_time =scatter(x=time_history, y=getindex.(ω_history_sapling,3), mode="lines", name="ω_z")
layout = Layout(title="Sapling BDot ω Propogation", xaxis_title="time [sec]", yaxis_title="ω [rad/sec]")
plot([ω_x_vs_time, ω_y_vs_time, ω_z_vs_time],layout)

Starting integration...
1.0
1.087557671447224
1.01446457609165
0.5859823561046935
0.4841295085194247
0.37153969786430574
0.3068305653066241
0.26828980162571725
0.25105882971628907
0.18885553729938087
0.17670964403987577
0.16373991424255774
0.15071417575540413
0.12434198861717216
0.11379578804365785
0.09555054402917772
0.09180503230092553
0.059835489925201935
0.04724222202921858
0.04324713768146249
0.032048266565763206
0.033784182555227416
0.03153247040815821
0.027179996811083185
0.018103984985711415
0.012341238775187892
0.010664701993144066
0.008170457032556144
0.006898066274741543
0.004987355531072879
0.004511514375256319
0.0036003665435324636
0.002967433791599805
0.002381008752721736
0.0018117333044450625
0.0014085043447573662
0.0012502028385996677
0.0011055123498221464
0.0008966054149370795
0.0008153639413920334
0.0005459455440545158
0.00045443715194837253
0.00042737041145324284
0.0003407880583033984
0.00021983353785037799
0.00019981089470844093
0.00019933695011975505
0.000128282238

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [25]:
# Use estimated magnetic feild measurments 
# given constant magnetic field, do -BDot torque for one time step and progate...should see angular velocity 

# define test initial conditions
ω_0 = [deg2rad(80.),deg2rad(80.),deg2rad(80.)] # rad/sec
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
# define initial orbital conditions
orbit = KeplarianOrbit(
                767.e3 + R_e,
                0.05,
                deg2rad(82.3),
                deg2rad(0.),
                deg2rad(0.),
                deg2rad(0)
                )

time = 59715.0 #[days] MJD
# convert to equinoctial
orbit_initial_equinoctial = Keplarian2Equinoctial(orbit)
orbit_initial = [orbit_initial_equinoctial.p,
                orbit_initial_equinoctial.f,
                orbit_initial_equinoctial.g,
                orbit_initial_equinoctial.h,
                orbit_initial_equinoctial.k,
                orbit_initial_equinoctial.L]
ECI_initial = Equinoctial2ECI(orbit_initial_equinoctial)[1:3]
ECEF_initial = ECI_to_ECEF(time, ECI_initial)
ECEF_hist = [ECEF_initial]


# propogate using RK45
time_initial = time # days
time_end = time_initial + ((60. * 60) / (24*60*60)) # stop integrator after 60 min
step_size = 10 # sec
ω_history_sapling = [ω_0]
quaternion_history_sapling = [quaternion_initial]
error_history_ω_sapling = [[0.,0.,0.]]
error_history_quaternion_sapling = [[0.,0.,0.]]
orbit_history = [orbit_initial]
error_history_orbit = [[0.,0.,0.,0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
while time < time_end
    global time = time_history[end]
    ω_sapling = ω_history_sapling[end]
    # equinoctial orbit numerical integration
    orbit = orbit_history[end]
    orbit_new, error = RK45(orbit, time, step_size, GaussVariationalEquationsEquinoctial)
    push!(orbit_history, orbit_new)
    push!(error_history_orbit, error)
    # convert to ECEF to determine ECEF magnetic field
    equinoctial_orbit = EquinoctialOrbit(orbit_new[1], orbit_new[2], orbit_new[3], orbit_new[4], orbit_new[5], orbit_new[6])
    ECI_orbit = Equinoctial2ECI(equinoctial_orbit)
    ECEF_orbit = ECI_to_ECEF(time, ECI_orbit[1:3])
    push!(ECEF_hist, ECEF_orbit)
    b_inertial = geomag_dipole(ECEF_orbit)/10^9
    b_inertial_norm = b_inertial/norm(b_inertial)
    B_dot_body_norm = cross(-ω_sapling,b_inertial_norm)/norm(cross(-ω_sapling,b_inertial_norm))
    M_sat = -(min(1 - (norm(ω_0)-norm(ω_sapling))/norm(ω_0),1)*B_dot_body_norm)
    M_B_dot_body = cross(M_sat,b_inertial)
    EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, M_B_dot_body)
    ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    if(norm(I_sapling.*ω_new_sapling) > norm(I_sapling.*ω_0))
        EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, [0,0,0])
        ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    end
    push!(time_history, time + step_size/(24*60*60))
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_sapling, error_sapling)
end
print("Integration finished!\n")

# plot numerical integration outputs
ω_x_vs_time = scatter(x=time_history.-time_history[1], y=getindex.(ω_history_sapling,1), mode="lines", name="ω_x")
ω_y_vs_time = scatter(x=time_history.-time_history[1], y=getindex.(ω_history_sapling,2), mode="lines", name="ω_y")
ω_z_vs_time =scatter(x=time_history.-time_history[1], y=getindex.(ω_history_sapling,3), mode="lines", name="ω_z")
layout = Layout(title="Sapling BDot ω Propogation", xaxis_title="time [days]", yaxis_title="ω [rad/sec]")
plot([ω_x_vs_time, ω_y_vs_time, ω_z_vs_time],layout)

Starting integration...
Integration finished!


data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [26]:
# plot norm
l_norms = []
for state in ω_history_sapling
    push!(l_norms, norm(I_sapling.*state))
end
norm_vs_time = scatter(x=time_history.-time_history[1], y=(l_norms.-l_norms[1])./l_norms[1] * 100, mode="lines", name="norm")
layout = Layout(title="Norms", xaxis_title="time [Days]", yaxis_title=" Percent Difference in L")
plot([norm_vs_time],layout)

data: [
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [27]:
# Use estimated magnetic feild measurments 
# given constant magnetic field, do -BDot torque for one time step and progate...should see angular velocity 

# define test initial conditions
ω_0 = [deg2rad(80.),deg2rad(80.),deg2rad(80.)] # rad/sec
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
# define initial orbital conditions
orbit = KeplarianOrbit(
                767.e3 + R_e,
                0.05,
                deg2rad(82.3),
                deg2rad(0.),
                deg2rad(0.),
                deg2rad(0)
                )

time = 59715.0 #[days] MJD
# convert to equinoctial
orbit_initial_equinoctial = Keplarian2Equinoctial(orbit)
orbit_initial = [orbit_initial_equinoctial.p,
                orbit_initial_equinoctial.f,
                orbit_initial_equinoctial.g,
                orbit_initial_equinoctial.h,
                orbit_initial_equinoctial.k,
                orbit_initial_equinoctial.L]
ECI_initial = Equinoctial2ECI(orbit_initial_equinoctial)[1:3]
ECEF_initial = ECI_to_ECEF(time, ECI_initial)
ECEF_hist = [ECEF_initial]


# propogate using RK45
time_initial = time # days
time_end = time_initial + ((60. * 60) / (24*60*60)) # stop integrator after 60 min
step_size = 10 # sec
ω_history_sapling = [ω_0]
quaternion_history_sapling = [quaternion_initial]
error_history_ω_sapling = [[0.,0.,0.]]
error_history_quaternion_sapling = [[0.,0.,0.]]
orbit_history = [orbit_initial]
error_history_orbit = [[0.,0.,0.,0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
while time < time_end
    global time = time_history[end]
    ω_sapling = ω_history_sapling[end]
    b_inertial = [7*10^-5,0,0]
    b_inertial_norm = b_inertial/norm(b_inertial)
    B_dot_body_norm = cross(-ω_sapling,b_inertial_norm)/norm(cross(-ω_sapling,b_inertial_norm))
    M_sat = -(min(1 - (norm(ω_0)-norm(ω_sapling))/norm(ω_0),1)*B_dot_body_norm)
    M_B_dot_body = cross(M_sat,b_inertial)
    EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, M_B_dot_body)
    ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    if(norm(I_sapling.*ω_new_sapling) > norm(I_sapling.*ω_0))
        EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, [0,0,0])
        ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    end
    push!(time_history, time + step_size/(24*60*60))
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_sapling, error_sapling)
end
print("Integration finished!\n")

# plot numerical integration outputs
ω_x_vs_time = scatter(x=time_history.-time_history[1], y=getindex.(ω_history_sapling,1), mode="lines", name="ω_x")
ω_y_vs_time = scatter(x=time_history.-time_history[1], y=getindex.(ω_history_sapling,2), mode="lines", name="ω_y")
ω_z_vs_time =scatter(x=time_history.-time_history[1], y=getindex.(ω_history_sapling,3), mode="lines", name="ω_z")
layout = Layout(title="Sapling BDot ω Propogation", xaxis_title="time [days]", yaxis_title="ω [rad/sec]")
plot([ω_x_vs_time, ω_y_vs_time, ω_z_vs_time],layout)

Starting integration...
Integration finished!


data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [28]:
# plot norm
l_norms = []
for state in ω_history_sapling
    push!(l_norms, norm(I_sapling.*state))
end
norm_vs_time = scatter(x=time_history.-time_history[1], y=(l_norms.-l_norms[1])./l_norms[1] * 100, mode="lines", name="norm")
layout = Layout(title="Norms", xaxis_title="time [Days]", yaxis_title=" Percent Difference in L")
plot([norm_vs_time],layout)

data: [
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [17]:
# Use estimated magnetic feild measurments 
# given constant magnetic field, do -BDot torque for one time step and progate...should see angular velocity 

# define test initial conditions
ω_0 = [deg2rad(3.),deg2rad(3.),deg2rad(3.)] # rad/sec
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
# define initial orbital conditions
orbit = KeplarianOrbit(
                767.e3 + R_e,
                0.,
                deg2rad(0.01),
                deg2rad(0.),
                deg2rad(0.),
                deg2rad(0)
                )

time = 59715.0 #[days] MJD
# convert to equinoctial
orbit_initial_equinoctial = Keplarian2Equinoctial(orbit)
orbit_initial = [orbit_initial_equinoctial.p,
                orbit_initial_equinoctial.f,
                orbit_initial_equinoctial.g,
                orbit_initial_equinoctial.h,
                orbit_initial_equinoctial.k,
                orbit_initial_equinoctial.L]
ECI_initial = Equinoctial2ECI(orbit_initial_equinoctial)[1:3]
ECEF_initial = ECI_to_ECEF(time, ECI_initial)
ECEF_hist = [ECEF_initial]


# propogate using RK45
time_initial = time # days
time_end = time_initial + ((10. * 60) / (24*60*60)) # stop integrator after 100 min
step_size = 1 # sec
ω_history_sapling = [ω_0]
quaternion_history_sapling = [quaternion_initial]
error_history_ω_sapling = [[0.,0.,0.]]
error_history_quaternion_sapling = [[0.,0.,0.]]
orbit_history = [orbit_initial]
error_history_orbit = [[0.,0.,0.,0.,0.,0.]]
time_history = [time_initial]

time = time_initial
print("Starting integration...\n")
while time < time_end
    global time = time_history[end]
    ω_sapling = ω_history_sapling[end]
    # equinoctial orbit numerical integration
    orbit = orbit_history[end]
    orbit_new, error = RK45(orbit, time, step_size, GaussVariationalEquationsEquinoctial)
    push!(orbit_history, orbit_new)
    push!(error_history_orbit, error)
    # convert to ECEF to determine ECEF magnetic field
    equinoctial_orbit = EquinoctialOrbit(orbit_new[1], orbit_new[2], orbit_new[3], orbit_new[4], orbit_new[5], orbit_new[6])
    ECI_orbit = Equinoctial2ECI(equinoctial_orbit)
    ECEF_orbit = ECI_to_ECEF(time, ECI_orbit[1:3])
    push!(ECEF_hist, ECEF_orbit)
    b_inertial = geomag_dipole(ECEF_orbit)/10^9
    b_inertial_norm = b_inertial/norm(b_inertial)
    B_dot_body_norm = cross(-ω_sapling,b_inertial_norm)/norm(cross(-ω_sapling,b_inertial_norm))
    M_sat = -(min(1 - (norm(ω_0)-norm(ω_sapling))/norm(ω_0),1)*B_dot_body_norm)
    M_B_dot_body = cross(M_sat,b_inertial)
    EulerEquations_sapling(ω, time) = EulerEquations(ω, time, I_sapling, M_B_dot_body)
    ω_new_sapling, error_sapling = RK45(ω_sapling, time, step_size, EulerEquations_sapling)
    push!(time_history, time + step_size/(24*60*60))
    push!(ω_history_sapling, ω_new_sapling)
    push!(error_history_sapling, error_sapling)
end
print("Integration finished!\n")

# plot numerical integration outputs
ω_x_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,1), mode="lines", name="ω_x")
ω_y_vs_time = scatter(x=time_history, y=getindex.(ω_history_sapling,2), mode="lines", name="ω_y")
ω_z_vs_time =scatter(x=time_history, y=getindex.(ω_history_sapling,3), mode="lines", name="ω_z")
layout = Layout(title="Sapling BDot ω Propogation", xaxis_title="time [sec]", yaxis_title="ω [rad/sec]")
plot([ω_x_vs_time, ω_y_vs_time, ω_z_vs_time],layout)

Starting integration...
Integration finished!


data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [18]:
# functions for RL Model
I_sapling = [0.00165567, 0.00167717, 0.00178716] # kg*m^2
ω_0 = [deg2rad(3.),deg2rad(3.),deg2rad(3.)] # rad/sec
b_norm = 7*10^-5 # Tesla
b_const = [1,0,0]

"""
    Euler Equations with applied torque conditions used with numerical propogator
    to propogate angular velocity
"""
function EulerEquations(ω, time, I, M)
    # calculate dω/dt
    dωdt = [(M[1]-((I[3]-I[2])*ω[2]*ω[3]))/I[1], (M[2]-((I[1]-I[3])*ω[3]*ω[1]))/I[2], (M[3]-((I[2]-I[1])*ω[1]*ω[2]))/I[3]]
end

# RKF45 constants (to be stored in seperate file)
const A2 = 2. / 9.
const A3 = 1. / 3.
const A4 = 3. / 4.
const A5 = 1.
const A6 = 5. / 6.
const B21 = 2. / 9.
const B31 = 1. / 12.
const B41 = 69. / 128.
const B51 = -17. / 12.
const B61 = 65. / 432.
const B32 = 1. / 4.
const B42 = -243. / 128.
const B52 = 27. / 4.
const B62 = -5. / 16.
const B43 = 135. / 64.
const B53 = -27. / 5.
const B63 = 13. / 16.
const B54 = 16. / 15.
const B64 = 4. / 27.
const B65  = 5. / 144.
const CH1 = 47. / 450.
const CH2 = 0.
const CH3 = 12. / 25.
const CH4 = 32. / 225.
const CH5 = 1. / 30.
const CH6 = 6. / 25.
const CT1 = -1. / 150.
const CT2 = 0.
const CT3 = 3. / 100.
const CT4 = -16. / 75.
const CT5 = -1. / 20.
const CT6 = 6. / 25.

# https://en.wikipedia.org/wiki/Runge%E2%80%93Kutta%E2%80%93Fehlberg_method
function RK45(x, time, step, dxdt)
    # compute k1 through k6
    k1 = step * dxdt(x, time)
    modifier = B21 * k1
    k2 = step * dxdt(x + modifier, time + (A2 * step))
    modifier = B31 * k1 + B32 * k2
    k3 = step * dxdt(x + modifier, time + (A3 * step))
    modifier = B41 * k1 + B42 * k2 + B43 * k3
    k4 = step * dxdt(x + modifier, time + (A4 * step))
    modifier = B51 * k1 + B52 * k2 + B53 * k3 + B54 * k4
    k5 = step * dxdt(x + modifier, time + (A5 * step))
    modifier = B61 * k1 + B62 * k2 + B63 * k3 + B64 * k4 + B65 * k5
    k6 = step * dxdt(x + modifier, time + (A6 * step))
    # compute weighted average
    x_new = x + CH1 * k1 + CH2 * k2 + CH3 * k3 + CH4 * k4 + CH5 * k5 + CH6 * k6
    # compute error
    error = abs.(CT1 * k1 + CT2 * k2 + CT3 * k3 + CT4 * k4 + CT5 * k5 + CT6 * k6)
    # NOTE: we can add in adaptive time steps here if we want...
    # return new x values and numerical integration error
    return(x_new, error)
end

function BDot_solution(B, ω; ω_0=ω_0)
    B_dot = cross(-ω,B)
    B_dot_body_norm = B_dot/norm(B_dot)
    M = -(1 - (norm(ω_0)-norm(ω))/norm(ω_0))*B_dot_body_norm
    return(M)
end

function Determine_ω(B, ω, M; time_step=1, I=I_sapling, time=0)
    # TODO: Calculate torque from moment -- add here
    EulerEquations_M(ω, time) = EulerEquations(ω, time, I, M)
    ω_new, error = RK45(ω, time, step_size, EulerEquations_M)
    return ω_new
end

function Calculate_Reward(ω_prev, ω_new, ω_0)
   reward = norm(ω_prev) - norm(ω_new)
   # ω_new < ω_0
   return reward 
end

Calculate_Reward (generic function with 1 method)